# Estimate wind speeds from flight data



In [1]:
from flightanalysis import Section
import plotly.express as px
from geometry import Points
from geometry import Point


secs = [
    Section.from_csv("examples/data/P23.csv").append_derived_values(),
    Section.from_csv("examples/data/loops.csv").append_derived_values(),
    Section.from_csv("examples/data/snap_roll_section.csv").append_derived_values(),
]


In [2]:
from flightplotting.plots import plotsec

plotsec(secs[0])

Difference between airspeed * body x axis and the velocity vector gives the wind vector. But, airspeed is not known. 

proposed solution - assume a wind field, direction and magnitude. Subtract the local wind speed from the body velocity vector. Resulting vector should have the same heading as the body x axis. use the direction and magnitude parameters as variables to minimize the heading error between the two vectors. 



In [33]:
import numpy as np
from flightanalysis.section.tools.wind import get_wind_error, wind_speed, wind_vector

h = np.linspace(0, 300, 1000)
vecs = Points(wind_vector(np.radians(30), h, 20).T)
vecdf = vecs.to_pandas()
vecdf.index = h
px.line(vecdf, width=500, height=300)

In [37]:
winds = [sec.calculate_wind() for sec in secs]

for wind in winds:
    print("v0={:.2f} m/s, heading={:.2f} deg, exponent={:.3f}".format(wind.speed, np.degrees(wind.heading), wind.a))

v0=2.38 m/s, heading=353.26 deg, exponent=0.190
v0=9.51 m/s, heading=343.75 deg, exponent=0.191
v0=2.38 m/s, heading=353.26 deg, exponent=0.190


In [31]:
sec = secs[0].flying_only()
less = sec.data.loc[sec.data.brvp.abs() < 0.5]

print(sec.data.brvp.abs().describe())
px.scatter(x=np.degrees(less.alpha), y=less.baz / (less.bvx**2), color=less.elevator).show()
#
# secs[0].bacc
#sec.data.brvp.describe()

count    13107.000000
mean         0.260736
std          0.275155
min          0.000012
25%          0.040368
50%          0.147181
75%          0.411409
max          1.472406
Name: brvp, dtype: float64


In [ ]:
from flightplotting.plots import plotsec
from geometry import Quaternion
from flightanalysis import State




def aerodynamic_parameters(state: State, wind_vec: Point):
    print("Atmospheric Wind Velocity in Sequence Frame = {}".format(wind_vec))

    body_wind_vec = state.att.inverse().transform_point(wind_vec) 
    print("Atmospheric Wind Velocity in Body Frame = {}".format(body_wind_vec))

    print("Velocity in Body Frame = {}".format(state.bvel))

    print("Velocity in World Frame = {}".format(state.att.transform_point(state.bvel)))

    body_oncoming_wind=state.bvel - body_wind_vec
    print("Body Wind Vector = {}".format(body_oncoming_wind))

    alpha = np.tan(body_oncoming_wind.z / body_oncoming_wind.x)
    beta = np.tan(body_oncoming_wind.y / body_oncoming_wind.x)
    print("Angle of Attack, Alpha = {}, Beta = {}".format(np.degrees(alpha), np.degrees(beta)) )

    print("Body Frame Accelerations (m/s**2) = {}".format(state.bacc *9.81 ))

    forces = 4.5 * state.bacc # 
    print("Body Frame Forces (kgf) = {}".format(forces / 9.81 ))

    #print("At this point need to s")

    body_to_stability = Quaternion.from_euler((0.0, alpha, 0.0))
    stability_to_wind = Quaternion.from_euler((0.0, 0.0, -beta))

    wind_force = stability_to_wind.transform_point(body_to_stability.transform_point(forces))

    print("Wind Axis Lift Force (kgf) = {}".format(wind_force / 9.81 ))



for name, state, wind in zip(names, states, wind_speeds):
    print(name)
    aerodynamic_parameters(state, wind)
    print("\n")

#plotsec(test, nmodels=5 )

In [ ]:
# alpha, beta, axis_rates, airspeed, control_deflections  - > forces + moments

In [ ]:
from flightplotting.plots import aoa_brv_plot
from flightplotting.traces import sec_col_trace
import plotly.graph_objects as go
from plotly.subplots import mQQake_subplots
import numpy as np
snap = schedule.manoeuvres[16].elements[2].get_data(aligned)
aoa_brv_plot(snap)

In [ ]:
import numpy as np
import pandas as pd

pd.DataFrame([]).reindex()